In [4]:
#importando bibliotecas utilizadas durano desenvolvimento 

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
sns.set_theme(style="darkgrid")

from sklearn.preprocessing import StandardScaler, LabelEncoder
from imblearn.under_sampling import RandomUnderSampler, NearMiss, OneSidedSelection
from imblearn.over_sampling import RandomOverSampler, SMOTE, BorderlineSMOTE
from collections import Counter

from sklearn.model_selection import GridSearchCV
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier

from sklearn.metrics import accuracy_score
from sklearn.metrics import confusion_matrix
from pandas_profiling import ProfileReport
from sklearn.linear_model import LogisticRegression
from sklearn.tree import DecisionTreeClassifier
from imblearn.over_sampling import SMOTE
from sklearn.svm import SVC
from sklearn import tree
from sklearn.ensemble import RandomForestClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.model_selection import GridSearchCV, cross_val_score
from sklearn.neural_network import MLPClassifier
from sklearn.gaussian_process.kernels import RBF
from sklearn.ensemble import AdaBoostClassifier
from sklearn.naive_bayes import GaussianNB
from sklearn.linear_model import SGDClassifier
from sklearn.discriminant_analysis import QuadraticDiscriminantAnalysis
from sklearn.model_selection import RepeatedStratifiedKFold
from sklearn.tree import DecisionTreeRegressor
from sklearn.tree import DecisionTreeClassifier
from sklearn.linear_model import LogisticRegression
import xgboost as xgb
from matplotlib import pyplot
from numpy import mean

In [5]:
#realizando leitura da base de dados
base_train =  pd.read_csv('data_products_train.csv')
base_test = pd.read_csv('data_products_test.csv')

In [6]:
#realizando analise exploratoria da base de treino
profile = ProfileReport(base_train)
profile

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [7]:
#realizando analise exploratoria da base de teste
profile_test = ProfileReport(base_test)
profile_test

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [8]:
#verificando os valores nulos
base_train[base_train.isnull().any(axis=1)]

category  product_name_lenght  \
16           moveis_decoracao                  NaN   
20            cama_mesa_banho                 55.0   
39              esporte_lazer                 60.0   
42     informatica_acessorios                  NaN   
52     informatica_acessorios                 56.0   
...                       ...                  ...   
11972            beleza_saude                 58.0   
11989               telefonia                 60.0   
11990                pet_shop                 59.0   
11991        moveis_decoracao                 54.0   
11996              brinquedos                 44.0   

       product_description_lenght  product_photos_qty  product_weight_g  \
16                         1722.0                 2.0             550.0   
20                          396.0                 1.0            3775.0   
39                         2099.0                 1.0            3600.0   
42                          227.0                 7.0             950.0   
52                          306.0                 5.0               NaN   
...                           ...                 ...               ...   
11972                      1692.0                 4.0               NaN   
11989                         NaN                 3.0             250.0   
11990                       780.0                 3.0             850.0   
11991                       441.0                 1.0            2900.0   
11996                       669.0                 2.0             700.0   

       product_length_cm  product_height_cm  product_width_cm  
16                  52.0               11.0              11.0  
20                   NaN               13.0              25.0  
39                   NaN               32.0              30.0  
42                  18.0                4.0              15.0  
52                  19.0               23.0              19.0  
...                  ...                ...               ...  
11972               18.0               10.0              14.0  
11989               19.0                3.0              11.0  
11990               50.0                5.0               NaN  
11991               40.0                NaN              30.0  
11996                NaN               30.0              30.0  

[1548 rows x 8 columns]

In [9]:
#verificando as descrição da base 
base_train.describe()

product_name_lenght  product_description_lenght  product_photos_qty  \
count         11765.000000                11776.000000        11742.000000   
mean             48.975436                  802.878482            2.095214   
std              10.143948                  664.000839            1.696089   
min               5.000000                    8.000000            1.000000   
25%              43.000000                  346.000000            1.000000   
50%              52.000000                  621.000000            1.000000   
75%              57.000000                 1015.000000            3.000000   
max              69.000000                 3985.000000           18.000000   

       product_weight_g  product_length_cm  product_height_cm  \
count      11779.000000       11758.000000       11767.000000   
mean        2019.026827          32.019816          15.807343   
std         3870.850412          17.738056          12.011844   
min            0.000000           8.000000           2.000000   
25%          300.000000          19.000000           8.000000   
50%          750.000000          26.000000          13.000000   
75%         1750.000000          40.000000          20.000000   
max        40425.000000         105.000000         105.000000   

       product_width_cm  
count      11766.000000  
mean          23.316930  
std           11.949352  
min            7.000000  
25%           15.000000  
50%           20.000000  
75%           30.000000  
max          118.000000

In [10]:
#transformando os valores nulos com a media da coluna base de treino 
base_train['product_name_lenght'] = base_train['product_name_lenght'].fillna(base_train['product_name_lenght'].mean())
base_train['product_description_lenght'] = base_train['product_description_lenght'].fillna(base_train['product_description_lenght'].mean())
base_train['product_photos_qty'] = base_train['product_photos_qty'].fillna(base_train['product_photos_qty'].mean())
base_train['product_weight_g'] = base_train['product_weight_g'].fillna(base_train['product_weight_g'].mean())
base_train['product_length_cm'] = base_train['product_length_cm'].fillna(base_train['product_length_cm'].mean())
base_train['product_height_cm'] = base_train['product_height_cm'].fillna(base_train['product_height_cm'].mean())
base_train['product_width_cm'] = base_train['product_width_cm'].fillna(base_train['product_width_cm'].mean())

In [11]:
#transformando os valores nulos com a media da coluna base de teste 
base_test['product_name_lenght'] = base_test['product_name_lenght'].fillna(base_test['product_name_lenght'].mean())
base_test['product_description_lenght'] = base_test['product_description_lenght'].fillna(base_test['product_description_lenght'].mean())
base_test['product_photos_qty'] = base_test['product_photos_qty'].fillna(base_test['product_photos_qty'].mean())
base_test['product_weight_g'] = base_test['product_weight_g'].fillna(base_test['product_weight_g'].mean())
base_test['product_length_cm'] = base_test['product_length_cm'].fillna(base_test['product_length_cm'].mean())
base_test['product_height_cm'] = base_test['product_height_cm'].fillna(base_test['product_height_cm'].mean())
base_test['product_width_cm'] = base_test['product_width_cm'].fillna(base_test['product_width_cm'].mean())

In [12]:
#contando os valores nulos
base_train.isnull().sum()

category                      0
product_name_lenght           0
product_description_lenght    0
product_photos_qty            0
product_weight_g              0
product_length_cm             0
product_height_cm             0
product_width_cm              0
dtype: int64

In [13]:
#contandos os valores nulos
base_test.isnull().sum()

category                      0
product_name_lenght           0
product_description_lenght    0
product_photos_qty            0
product_weight_g              0
product_length_cm             0
product_height_cm             0
product_width_cm              0
dtype: int64

In [14]:

#criando base de treino e teste

colunas = ['product_name_lenght', 'product_description_lenght', \
       'product_photos_qty', 'product_weight_g', 'product_length_cm', \
       'product_height_cm', 'product_width_cm']

X_train = base_train.loc[:, colunas].values
y_train = base_train.loc[:, 'category'].values

X_test = base_test.loc[:, colunas].values
y_test = base_test.loc[:, 'category'].values

In [15]:
oversample = SMOTE(random_state=42)
X, y = oversample.fit_resample(X_train, y_train)

In [18]:
print ('X_train: numero de linhas e colunas: {}'.format(X_train.shape))
print ('X_test: numero de linhas e colunas: {}'.format(X_test.shape))
print ('y_train: numero de linhas e colunas: {}'.format(y_train.shape))
print ('y_test: numero de linhas e colunas: {}'.format(y_test.shape))

X_train: numero de linhas e colunas: (12000, 7)
X_test: numero de linhas e colunas: (3000, 7)
y_train: numero de linhas e colunas: (12000,)
y_test: numero de linhas e colunas: (3000,)


In [21]:
#normalizando a bases de treino e texte
sc = StandardScaler()    
X_train = sc.fit_transform(X_train)

X_test = sc.transform(X_test) 


In [22]:
# preparando o  modelo.
clf = RandomForestClassifier(criterion="gini", 
                         n_estimators = 800,
                         min_samples_split = 2,
                         min_samples_leaf = 1,
                         max_features = 'sqrt',
                         max_depth = 20,
                         bootstrap = False)
#fitando o modelo
clf = clf.fit(X_train, y_train)

In [23]:
y_previsao= clf.predict(X_test)
y_probi = clf.predict_proba(X_test)

In [24]:
# Obtenha a acurácia do modelo
print('Accuracy: %.2f' % accuracy_score(y_test, y_previsao))

Accuracy: 0.59


In [26]:
#criando um array com os valores previsto
vPredict = np.array(y_previsao)
vPredict

array(['beleza_saude', 'automotivo', 'esporte_lazer', ..., 'brinquedos',
       'beleza_saude', 'moveis_decoracao'], dtype=object)

In [28]:
#criando um array com a probabilidade dos valores
vProba = np.array(y_probi)
vProba

array([[3.35275019e-03, 3.87119620e-02, 4.88625770e-01, ...,
        3.75474946e-02, 1.09696016e-02, 5.12496898e-02],
       [0.00000000e+00, 2.83261536e-01, 1.13041454e-01, ...,
        3.32582498e-02, 9.36490354e-02, 2.64701982e-01],
       [3.04559178e-04, 1.52402214e-03, 8.42813123e-03, ...,
        1.82497608e-02, 4.25349752e-03, 2.55102041e-05],
       ...,
       [6.27155172e-03, 7.24803649e-02, 4.19767812e-02, ...,
        8.66731289e-02, 1.70389658e-02, 2.74436090e-03],
       [3.86043233e-03, 3.14642752e-02, 3.80607912e-01, ...,
        6.33784801e-02, 1.18379219e-01, 4.05449569e-03],
       [0.00000000e+00, 0.00000000e+00, 0.00000000e+00, ...,
        9.98750000e-01, 0.00000000e+00, 0.00000000e+00]])

In [29]:
#criando um array com os maiores valores 
vMaiores = []
for values in vProba:
  vMaiores.append(values.max())

In [30]:
vMaior = np.array(vMaiores)
vMaior

array([0.48862577, 0.28326154, 0.94848672, ..., 0.26007172, 0.38060791,
       0.99875   ])

In [32]:
#trazendo accuracy depois do tratamento
print('Accuracy: %.2f' % accuracy_score(y_test[vMaior > 0.45], y_previsao[vMaior > 0.45]))

Accuracy: 0.83
